# Netlify and heroku; together and free

Let's say you want to do this:

- You have an API, probably built in flask that you want to deploy to [heroku](https://www.heroku.com/).
- You have a UI that calls this API, maybe built using Vue or React and you want to deploy this to [netlify](https://www.netlify.com/)

If you're like me you can't really afford servers for personal projects so services like heroku and netlify that offer free tiers are your lifeline.

The problem with setting up this project is this:

- Netlify has limited build minutes in it's free account. You can't expect to frequently deploy an application that takes a long time to build.
- Heroku and netlify both use runtime.txt to define what the runtime environment should use. This would have been fine but they both have incompatible names for the same thing. For example heroku says I should type `python-3.8` and netlify says something different.

## Solution

- Use gitlab to host your code. I'm assuming you have a `api` folder that contains api code and `site` folder that holds your vue code.
- Set up a [gitlab runner](https://docs.gitlab.com/runner/install/) on a machine you own. I use my laptop for this.
- Disable public runners in the `Settings -> CICI` section of your gitlab project.
- Add a [deploy key](https://docs.gitlab.com/ee/user/project/deploy_keys/) to your project. Make sure it can push to the project. This will be used to push code to the gitlab repo.

With this much done we need to now write a gitlab CI job that will:

- Build your UI using something like `yarn build`.
- Commit the public files to git.
- Create a new branch `deploy-netlify` from this new commit that contains your built site.
- Run `git push origin deploy-netlify --force`

After this

- Netlify can now be set up to auto deploy from the `deploy-netlify` branch and use the `site/public` or `site/dist` folder to serve the website.
- You can do a similar setup for heroku where you use the branch `deploy-heroku` instead of `deploy-netlify`.


The benefits of this setup are:

- Zero cost. No netlify pipeline minutes are used.
- No gitlab pipeline quota is used since you are running on your own machine.
- No conflict with heroku. Each deploy lives on a separate branch and you can use pipeline jobs to ensure they are in sync.